# `bismark` Parameter Testing

In this notebook I'll test different `bismark` alignment parameters on a subset of Pacific oyster (*C. gigas*) Whole Genome Bisulfite Sequencing data.

# 0. Set working directory

In [1]:
pwd

'/Users/yaamini/Documents/project-gigas-oa-meth/notebooks'

In [2]:
cd ../analyses/

/Users/yaamini/Documents/project-gigas-oa-meth/analyses


In [3]:
mkdir 2019-08-30-Bismark-Parameter-Testing

In [4]:
cd 2019-08-30-Bismark-Parameter-Testing/

/Users/yaamini/Documents/project-gigas-oa-meth/analyses/2019-08-30-Bismark-Parameter-Testing


## 1. Download files

Sam already prepared the *C. gigas* bisulfite genome needed for `bismark`, so I'm going to download it. Creation details can be found [here](https://robertslab.github.io/sams-notebook/2019/02/21/Data-Management-Create-C.gigas-Bisulfite-Genome-with-Bismark-on-Mox.html).

In [6]:
#C. gigas bisulfite genome
!curl http://owl.fish.washington.edu/halfshell/genomic-databank/Crassostrea_gigas.oyster_v9.dna_sm.toplevel_bisulfite.tar.gz \
> Crassostrea_gigas.oyster_v9.dna_sm.toplevel_bisulfite.tar.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1449M  100 1449M    0     0  4786k      0  0:05:10  0:05:10 --:--:-- 5709k


In [7]:
!gunzip Crassostrea_gigas.oyster_v9.dna_sm.toplevel_bisulfite.tar.gz

In [10]:
!tar --extract Crassostrea_gigas.oyster_v9.dna_sm.toplevel_bisulfite.tar

^C


In [12]:
!ls -F

Crassostrea_gigas.oyster_v9.dna_sm.toplevel/
Crassostrea_gigas.oyster_v9.dna_sm.toplevel_bisulfite.tar


In [16]:
#The bisulfite genome is in this directory, along with the original genome and the script used to create it
!ls -F Crassostrea_gigas.oyster_v9.dna_sm.toplevel/

20190221_cgigas_genome_prep_bismark.sh
Bisulfite_Genome/
Crassostrea_gigas.oyster_v9.dna_sm.toplevel.fa
Crassostrea_gigas.oyster_v9.dna_sm.toplevel.fa.fai
readme.txt


Sam also trimmed the WGBS data! I'm going to download the trimmed files. Creation details can be found [here](https://robertslab.github.io/sams-notebook/2019/04/15/FastQC-WGBS-Sequencing-Data-from-Genewiz-Received-20190408.html).

In [26]:
#Ambient pH file 1. There are 2 files per sample sent.
!curl http://owl.fish.washington.edu/nightingales/C_gigas/YRVA_R1_001.fastq.gz > YRVA_R1_001.fastq.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 5621M  100 5621M    0     0  3063k      0  0:31:18  0:31:18 --:--:-- 6888k


In [27]:
#Ambient pH file 2. There are 2 files per sample sent.
!curl http://owl.fish.washington.edu/nightingales/C_gigas/YRVA_R2_001.fastq.gz > YRVA_R2_001.fastq.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 6018M  100 6018M    0     0  2833k      0  0:36:14  0:36:14 --:--:-- 5700k


In [28]:
#Low pH file 1
!curl http://owl.fish.washington.edu/nightingales/C_gigas/YRVL_R1_001.fastq.gz > YRVL_R1_001.fastq.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 5554M  100 5554M    0     0  1832k      0  0:51:43  0:51:43 --:--:-- 2567k


In [29]:
#Low pH file 2
!curl http://owl.fish.washington.edu/nightingales/C_gigas/YRVL_R2_001.fastq.gz > YRVL_R2_001.fastq.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 5969M  100 5969M    0     0  2063k      0  0:49:22  0:49:22 --:--:-- 5958k


## 2. Test alignment parameters

In [40]:
! /Users/Shared/Apps/Bismark_v0.19.0/bismark -help



     This program is free software: you can redistribute it and/or modify
     it under the terms of the GNU General Public License as published by
     the Free Software Foundation, either version 3 of the License, or
     (at your option) any later version.

     This program is distributed in the hope that it will be useful,
     but WITHOUT ANY WARRANTY; without even the implied warranty of
     MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
     GNU General Public License for more details.
     You should have received a copy of the GNU General Public License
     along with this program.  If not, see <http://www.gnu.org/licenses/>.



DESCRIPTION


The following is a brief description of command line options and arguments to control the Bismark
bisulfite mapper and methylation caller. Bismark takes in FastA or FastQ files and aligns the
reads to a specified bisulfite genome. Sequence reads are transformed into a bisulfite converted forward strand
version (C->T co

**What I need for this command**:

1. The path to bismark
2. --non_directional: See this issue
3. -p 4: Number of simultaneous threads to run
4. -u 10000: Only aligning the first 10,000 reads to test parameters
5. -score_min: I will run this with three different options: L,0,-0.6; L,0,-0.9; L,0,-1.2 to see how this impacts mapping efficiency
6. --genome + path to the folder with the .fa genome, which also has all of the bisulfite genome directories
7. -1 + Path to first paired file
8. -2 + Path to second paired file
9. Path to redirect standard error output.

### 2a. `score_min` = L,0,-0.6

In [46]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-0.6 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVA_R1_001.fastq.gz \
-2 YRVA_R2_001.fastq.gz \
2> bismark-A-0830-L006.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

In [47]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-0.6 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVL_R1_001.fastq.gz \
-2 YRVL_R2_001.fastq.gz \
2> bismark-L-0830-L006.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

Mapping efficiency is about 47%.

### 2b. `score_min` = L,0,-0.9

In [48]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-0.9 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVA_R1_001.fastq.gz \
-2 YRVA_R2_001.fastq.gz \
2> bismark-A-0830-L009.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

In [49]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-0.9 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVL_R1_001.fastq.gz \
-2 YRVL_R2_001.fastq.gz \
2> bismark-L-0830-L009.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

Mapping efficiency is about 61%.

### 2c. `score_min` = L,0,-1.2

In [50]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-1.2 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVA_R1_001.fastq.gz \
-2 YRVA_R2_001.fastq.gz \
2> bismark-A-0830-L012.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

In [51]:
%%bash

/Users/Shared/Apps/Bismark_v0.19.0/bismark \
--non_directional \
-p 4 \
-u 10000 \
-score_min L,0,-1.2 \
--genome Crassostrea_gigas.oyster_v9.dna_sm.toplevel/ \
-1 YRVL_R1_001.fastq.gz \
-2 YRVL_R2_001.fastq.gz \
2> bismark-L-0830-L012.err

FastQ format assumed (by default)
Each Bowtie 2 instance is going to be run with 4 threads. Please monitor performance closely and tune down if needed!
chr scaffold22 (1964558 bp)
chr scaffold1009 (1861391 bp)
chr scaffold150 (1854615 bp)
chr scaffold1024 (1774716 bp)
chr scaffold102 (1727112 bp)
chr scaffold419 (1725835 bp)
chr scaffold1532 (1715538 bp)
chr scaffold86 (1697160 bp)
chr scaffold337 (1638316 bp)
chr scaffold77 (1619719 bp)
chr scaffold257 (1615106 bp)
chr scaffold198 (1589021 bp)
chr scaffold1301 (1559340 bp)
chr scaffold962 (1469792 bp)
chr scaffold591 (1432801 bp)
chr scaffold501 (1397941 bp)
chr scaffold1213 (1372454 bp)
chr scaffold1179 (1367275 bp)
chr scaffold3 (1336734 bp)
chr scaffold481 (1334154 bp)
chr scaffold1599 (1324113 bp)
chr scaffold433 (1285081 bp)
chr scaffold471 (1282308 bp)
chr scaffold211 (1275876 bp)
chr scaffold393 (1263635 bp)
chr scaffold601 (1259944 bp)
chr scaffold142 (1252394 bp)
chr scaffold301 (1229110 bp)
chr scaffold53 (1214666 bp)
chr sc

Mapping efficiency is about 69%.

The biggest jump was from L,0,-0.6 to L,0,-0.9, so I will stick with L,0,-0.9.